# Modellierungsprojekt Optimierungsverfahren, Modellierung und Simulation

## Organisatorisches
In dieser Übung sollen Sie verschiedene dynamische Energiespeicherprobleme als gemischt-ganzzahlige Programme modellieren, mit Gurobi lösen und die Lösung visualisieren und interpretieren.

Die Abgabe erfolgt in Form eines Jupyter-Notebooks. Nutzen Sie den Markup-Modus, um ihre mathematische Modellierung zu beschreiben. Mathematische Formeln können Sie zwischen zwei `$`-Zeichen oder zwei doppelten Dollarzeichen `$$` setzen. Sie können auch per Copy-and-paste Markup-Codeschnipsel kopieren, z.B. aus den Übungsblättern.

Die Abgabe erfolgt in Teams von bis zu 4 Personen, die in ILIAS registriert werden müssen. Die Notebooks müssen bis **Montag, 19.06.2022, 18:00** in ILIAS abgegeben werden. 

Die Veranstaltungstermine am 09.06. sowie in der Woche ab dem 12.06. sind für die Arbeit am Projekt vorgesehen. Ich bin während der Termine vor Ort und stehe für Rückfragen und Unterstützung zur Verfügung. In den Veranstaltungsterminen in der Woche ab dem 19.06.2023 werde ich Sie in Einzelgesprächen (in Präsenz) zu ihrer abgegebenen Lösung befragen (ca. 10-15 Minuten). Die Termine bekommen Sie separat mitgeteilt.

Insgesamt gibt es 100 Punkte auf das Projekt, wobei 50 Punkte für eine 4.0 erforderlich sind. Folgende Aspekte werden für die Punktevergabe berücksichtigt:
- Korrektheit des mathematischen Modells
- Korrektheit der Implementierung
- Interpretation der Ergebnisse
- Darstellung, Übersichtlichkeit und Verständlichkeit des abgegebenen Jupyter Notebooks
- Einzelgespräche

Die Punktzahlen der einzelnen Aufgaben (z.B. 10+5) beziehen sich auf Punkte für die Abgabe plus Punkte für die (mündliche) Beantwortung von Fragen zu den Aufgaben in den Einzelgesprächen. Mögliche Fragen sind z.B.:

- "Wie haben Sie Bedingung X aus der Aufgabe im Modell realisiert?"
- "Was bedeutet die Constraint Y in Ihrem Modell?"
- "Was bedeuten die Terme in der Zielfunktion?"
- etc.

Das Projekt macht 30\% der Modulnote aus.

## Ausgangssituation
Sie sind Assistent der Geschäftsführung in einem mittelständischen Unternehmen. An einem Standort Ihrer Firma wurde kürzlich eine Photovoltaikanlage auf den Dächern der Gebäude sowie ein 100 kWh Stromspeicher (Batterie) installiert. Die PV-Anlage soll vorrangig dafür verwendet werden, um den Strombedarf des Standorts zu decken. Wenn die PV-Anlage mehr Strom produziert als der Standort gerade benötigt, wird damit der Stromspeicher geladen oder der Strom ins Netz eingespeist. Für das Einspeisen bekommen Sie eine Vergütung von 4 ct/kWh. Falls der Standort mehr Strom benötigt als die PV-Anlage produziert und die Batterie leer ist, so beziehen Sie Strom für 22 ct/kWh aus dem Netz. Schematisch sieht das Ganze so aus:

<div>
<img src="Aufgabe1.png" width="750"/>
</div>

Die Batterie hat eine Effizienz von 90% beim Be- und Entladen. Das bedeutet, dass für jede kWh Strom, die in der Batterie gespeichert wird, der Ladezustand um 0.9 kWh steigt. Umgekehrt kann mit einer 1 kWh aus der Batterie nur 0.9 kWh Bedarf gedeckt werden. Die Batterie kann mit einer Maximalleistung von 50kW ge- bzw. entladen werden, d.h. während einer Stunde muss die Summe aller Lastflüsse in und aus der Batterie kleiner als 50 kWh sein.

Ihr Chef hat gelesen, dass es mit Hilfe eines dynamischen Strompreistarifs möglich ist, den Betrieb der Anlage und die Energieversorgung des Standorts zu optimieren. Er bittet Sie, der Sache nachzugehen.

## ✏ Aufgabe 0: Datenanalyse (5 Punkte)
Sie möchten zunächst das System abbilden, wie es heute arbeitet. Dafür besorgen Sie sich historische Daten über den Stromverbrauch des Standorts (`Last [kWh]`) sowie Daten über die Sonneneinstrahlung, aus der Sie die Stromproduktion der PV-Anlage errechnen (`Solar [kWh]`). Alle Daten sind stundengenau für ein Jahr in der Datei `energy_2020.pkl` hinterlegt. In der Spalte `Preis [EUR/kWh]` ist zusätzlich der variable Strompreis für jede Stunde gegeben. Diesen benötigen Sie erst später.

In [1]:
import pandas as pd
import numpy as np  
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
df = pd.read_pickle("energy_2020_corrected.pkl")
df

Datum (MEZ)  Solar [kWh]  Preis [EUR/kWh]  Last [kWh]
0    2020-01-01 00:00:00+01:00          0.0          0.20940     94.2636
1    2020-01-01 01:00:00+01:00          0.0          0.19300     92.4732
2    2020-01-01 02:00:00+01:00          0.0          0.18275     90.2108
3    2020-01-01 03:00:00+01:00          0.0          0.16160     87.5294
4    2020-01-01 04:00:00+01:00          0.0          0.15425     86.8490
...                        ...          ...              ...         ...
8779 2020-12-31 19:00:00+01:00          0.0          0.29735    120.8536
8780 2020-12-31 20:00:00+01:00          0.0          0.28350    112.4558
8781 2020-12-31 21:00:00+01:00          0.0          0.26220    106.1954
8782 2020-12-31 22:00:00+01:00          0.0          0.25930    103.6396
8783 2020-12-31 23:00:00+01:00          0.0          0.26130     98.7446

[8784 rows x 4 columns]

Bearbeiten Sie folgende Aufgaben:
1. Visualiseren Sie die drei Zeitreihen.
1. Wie hoch war der Gesamtstromverbrauch des Standorts im Jahr 2020?
1. Wie hoch wären die Gesamtstromkosten des Standorts im Jahr 2020 ohne PV-Anlage gewesen (d.h. mit 22 ct/kWh Strompreis)?
1. Wie hoch wäre die gesamte produzierte Strommenge der PV-Anlage im Jahr 2020 gewesen?
1. Wie hoch war der durchschnittliche Strompreis im Jahr 2020?

In [2]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Erstellen der Subplots
fig = make_subplots(rows=3, cols=1)

# Hinzufügen der Line Plots zu den Subplots
fig.add_trace(go.Scatter(x=df["Datum (MEZ)"], y=df["Solar [kWh]"], mode='lines'), row=1, col=1)
fig.add_trace(go.Scatter(x=df["Datum (MEZ)"], y=df["Preis [EUR/kWh]"], mode='lines'), row=2, col=1)
fig.add_trace(go.Scatter(x=df["Datum (MEZ)"], y=df["Last [kWh]"], mode='lines'), row=3, col=1)

# Anpassung der Layout-Eigenschaften
fig.update_layout(height=800,  title_text="Visualisierung der Daten")

fig.update_traces(
    name="Solar [kWh]",
    row=1, col=1,
    hovertemplate="<b>Petal Length</b>: %{x}<br><b>Petal Width</b>: %{y}<extra></extra>"
)
fig.update_traces(
    name="Preis [EUR/kWh]",
    row=2, col=1,
    #hovertemplate="<b>Sepal Length</b>: %{x}<br><b>Sepal Width</b>: %{y}<extra></extra>"
)
fig.update_traces(
    name="Last [kWh]",
    row=3, col=1
)

# Anzeigen der Subplots
fig.show()

In [8]:
df["Datum (MEZ)"].dt.year == 2020

0       True
1       True
2       True
3       True
4       True
        ... 
8779    True
8780    True
8781    True
8782    True
8783    True
Name: Datum (MEZ), Length: 8784, dtype: bool

In [11]:
#2.
df.loc[df["Datum (MEZ)"].dt.year == 2020]["Last [kWh]"].sum()

1043805.6564

In [12]:
#3.
df.loc[df["Datum (MEZ)"].dt.year == 2020]["Last [kWh]"].sum() * 0.22

229637.244408

In [14]:
#4.
df["Solar [kWh]"].sum()

970692.484

In [15]:
#5.
df["Preis [EUR/kWh]"].mean()

0.1523535746812386

## ✏ Aufabe 1: Basismodell (25+10 Punkte)
Modellieren Sie das System als lineares Programm, so dass die Gesamtstromkosten minimiert werden. Der Strombedarf des Standorts muss zu jedem Zeitpunkt 100% gedeckt werden. Gehen Sie vereinfachend davon aus, dass die Batterie zu Beginn des betrachteten Zeitraums eine Ladestand von 0 hat. 

1. Formulieren Sie ein lineares Programm in mathematischer Notation an, welches das Problem löst (Indexmengen, Problemdaten, Variablen, Zielfunktion, Nebenbedingungen).
2. Lösen Sie das Problem mit Gurobi, lesen Sie folgende Größen aus der Lösung aus, und visualisieren Sie sie:
   - Ladezustand der Batterie zu jedem Zeitpunkt $t$.
   - Menge an ein- bzw. ausgespeichertem Strom zu jedem Zeitpunkt $t$.
   - Strombezug und Stromverkauf an den Netzbetreiber zu jedem Zeitpunkt $t$.
   - Menge an selbst verbrauchtem Strom aus der PV-Anlage zu jedem Zeitpunkt $t$.
3. Geben Sie außerdem für das Jahr 2020 die folgenden Kenngrößen an:
   - Eigenverbrauch gesamt (in kWh)
   - Eigenverbrauch aus der Batterie (in kWh)
   - Gesamtstromkosten des Standorts mit PV-Anlage und Batterie (in EUR)
   - Ersparnis durch Eigenverbrauch gesamt (in EUR)
   - Ersparnis durch Eigenverbrauch aus der Batterie (in EUR)

$$
x_{ij}=\begin{cases}
1 & \text{Arbeitsaufgabe $i$ wird auf Maschine $j$ ausgeführt} \\
0 & \, \text{sonst}
\end{cases}
$$

Vollständiges MILP:
\begin{alignat*}{5}
\min          & \quad  &   k_{8784} &          \\[4mm]
\text{s.t. } & &  \sum_{i=1}^n d_ix_{ij} & \leq y,\quad\text{für }j=1,\dots, 4  \\[2mm]
& &  \sum_{i=1}^4 x_{ij} & = 1,\quad\text{für }i=1,\dots, n \\[2mm]
& &  \sum_{i=1}^4 x_{ij} & = 1,\quad\text{für }i=1,\dots, n \\[2mm]
& &  x_{ij} & \in \{0,1\},\quad\text{für }i=1,\dots, n,\ j=1,\dots,4
\end{alignat*}

\begin{alignat*}{5}
\min          & \quad  &   k_{8784} &          \\[4mm]
% Weitere Gleichungen und Restriktionen können hier eingefügt werden
k_{t+1} &= k_t + 0.22 \cdot E_t - 0.04 \cdot s_{vt} \\
% Weitere Gleichungen und Restriktionen können hier eingefügt werden
\end{alignat*}

# Aufgabe1
Formulieren Sie die Problemstellung als ganzzahliges lineares Programm.

Entscheidungsvariablen:

$l_t$ Steht für unseren Strombedarf den unsere Anlage zu dem Zeitpunkt t benötigt.

$s_t$ Steht für unseren erzeugte Strommenge durch unsere Solaranlage zu dem Zeitpunkt t.

$s_t^v$ Steht für unsere Strommmenge, die wir zu dem Zeitpunkt t verkaufen.

$s_t^e$ Steht für unsere Strommmenge an Solarstrom, die wir zu dem Zeitpunkt t verbrauchen.

$p_t^+$ Steht für den Preis den wir für unseren Strom zu dem Zeitpunkt t bekommen.

$p_t^-$ Steht für den Preis den wir für unseren Strom zu dem Zeitpunkt t bezahlen.

$k$ Steht für unseren Stromkosten.

$E_t$ Steht für unsere eingekaufte Strommenge zu dem Zeitpunkt t.

$b$ Steht für den Ladestand unserer Batterie.

$b_t^+$ Steht für den die Strommenge die in unsere Batterie fließt.

$b_t^-$ Steht für den die Strommenge die aus unserer Batterie fließt.



Vollständiges MILP:
\begin{alignat*}{5}
\min          & \quad  &   k_{8784} &          \\[4mm]
% Weitere Gleichungen und Restriktionen können hier eingefügt werden
k_{t+1} &= k_t + 0.22 \cdot E_t - 0.04 \cdot s_t^v \\
E_t &= l_t - 0.9 \cdot b_t^- - s_t^e \\
E_t &\geq 0 \\
b_{t+1} &= b_t + 0.9 \cdot b_t^+ - b_t^- \\
b_{t+1} &\leq 100 \\
b_{t+1} &\geq 0 \\
s_t &= s_t^v + s_t^e + b_t^+ \\
{b_t^+ \over 0.9}   + b_t^- &\leq 50 \\
b_t^- &\geq 0 \\
b_t^+ &\geq 0 \\
b_0 &= 0 \\
% Weitere Gleichungen und Restriktionen können hier eingefügt werden
\end{alignat*}


In [7]:
df.count()  

Datum (MEZ)        8784
Solar [kWh]        8784
Preis [EUR/kWh]    8784
Last [kWh]         8784
dtype: int64

## Aufgabe 2

In [20]:
import gurobipy as gp
from gurobipy import GRB

# Erzeugung des Modells
model = gp.Model("Strombedarfs-Optimierung")

# Entscheidungsvariablen
T = 8784  # Anzahl der Zeitschritte
l = model.addVars(T, name="l")  # Strombedarf
s = model.addVars(T, name="s")  # Erzeugte Strommenge durch Solaranlage
sv = model.addVars(T, name="sv")  # Verkaufte Strommenge
se = model.addVars(T, name="se")  # Verbrauchte Solarstrommenge
pt_plus = model.addVars(T, name="pt_plus")  # Preis für verkauften Strom
pt_minus = model.addVars(T, name="pt_minus")  # Preis für gekauften Strom
k = model.addVars(T, name="k", lb = 0)  # Stromkosten
E = model.addVars(T, name="E", lb = 0)  # Eingekaufte Strommenge
b = model.addVars(T +1, name="b", lb = 0, ub = 100)  # Ladestand der Batterie
bp = model.addVars(T, name="bp", lb = 0)  # Strommenge, die in die Batterie fließt
bm = model.addVars(T, name="bm", lb = 0)  # Strommenge, die aus der Batterie fließt

l_values = df["Last [kWh]"].values
s_values = df["Solar [kWh]"].values
model.addConstrs(l[t] == l_values[t] for t in range(T))
model.addConstrs(s[t] == s_values[t] for t in range(T))
# Constraints
model.addConstrs(k[t+1] == k[t] + 0.22 * E[t] - 0.04 * sv[t] for t in range(T-1))
model.addConstrs(E[t] == l[t] - 0.9 * bm[t] - se[t] for t in range(T))
model.addConstrs(E[t] >= 0 for t in range(T))
model.addConstrs(b[t+1] == b[t] + 0.9 * bp[t] - bm[t] for t in range(T-1))
#model.addConstrs(b[t] <= 100 for t in range(T))
#model.addConstrs(b[t] >= 0 for t in range(T))
model.addConstrs(s[t] == sv[t] + se[t] + bp[t] for t in range(T))
model.addConstrs(bp[t] / 0.9 + bm[t] <= 50 for t in range(T))
#model.addConstrs(bm[t] >= 0 for t in range(T))
#model.addConstrs(bp[t] >= 0 for t in range(T))
model.addConstr(b[0] == 0)

<gurobi.Constr *Awaiting Model Update*>

In [21]:
# Zielfunktion
model.setObjective(k[T-1], GRB.MINIMIZE)

In [22]:
model.update()

In [23]:
# Lösung des Modells
model.optimize()

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: AMD Ryzen 7 5700U with Radeon Graphics, instruction set [SSE2|AVX|AVX2]
Thread count: 8 physical cores, 16 logical processors, using up to 16 threads

Optimize a model with 70271 rows, 96625 columns and 184457 nonzeros
Model fingerprint: 0xcdd50ddb
Coefficient statistics:
  Matrix range     [4e-02, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+02, 1e+02]
  RHS range        [2e-03, 7e+02]
Presolve removed 54080 rows and 70954 columns
Presolve time: 0.11s
Presolved: 16191 rows, 25671 columns, 58929 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 3.409e+04
 Factor NZ  : 1.695e+05 (roughly 20 MB of memory)
 Factor Ops : 2.485e+06 (less than 1 second per iteration)
 Threads    : 6

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Co

In [36]:
b_values = [b[t].x for t in range(T + 1)]
bp_values = [bp[t].x for t in range(T)]
bm_values = [bm[t].x for t in range(T)]
sv_values = [sv[t].x for t in range(T)]
se_values = [se[t].x for t in range(T)]
E_values = [E[t].x for t in range(T)]
df_1 = df.copy()
df_1["B"] = b_values[:-1]
df_1["BP"] = bp_values
df_1["BM"] = bm_values
df_1["SV"] = sv_values
df_1["SE"] = se_values
df_1["E"] = E_values
rolling_mean_b = df_1['B'].rolling(window=5, min_periods=1).mean()
rolling_mean_bp = df_1['BP'].rolling(window=5, min_periods=1).mean()
rolling_mean_bm = df_1['BM'].rolling(window=5, min_periods=1).mean()
rolling_mean_sv = df_1['SV'].rolling(window=5, min_periods=1).mean()
rolling_mean_se = df_1['SE'].rolling(window=5, min_periods=1).mean()
rolling_mean_E = df_1['E'].rolling(window=5, min_periods=1).mean()

In [28]:


# Plotly-Figur erstellen
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_1['Datum (MEZ)'], y=df_1['B'], name='Werte von b'))
fig.add_trace(go.Scatter(x=df_1['Datum (MEZ)'], y=rolling_mean_b, name='Gleitender Durchschnitt'))

# Layout anpassen
fig.update_layout(
    title='Werte von b über die Zeit',
    xaxis_title='Zeitschritt',
    yaxis_title='Wert von b',
    hovermode='x'
)

# Plot anzeigen
fig.show()

In [35]:
# Erstellen der Subplots
fig = make_subplots(rows=2, cols=1)

# Hinzufügen der Line Plots zu den Subplots
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=df_1.BP, mode='lines'), row=1, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=rolling_mean_bp, mode='lines'), row=1, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=df_1.BM, mode='lines'), row=2, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=rolling_mean_bm, mode='lines'), row=2, col=1)



# Anpassung der Layout-Eigenschaften
fig.update_layout(height=800,  title_text="Visualisierung der Daten")

fig.update_traces(
    name="BP",
    row=1, col=1,
)
fig.update_traces(
    name="BM",
    row=2, col=1,
)

# Anzeigen der Subplots
fig.show()

In [38]:
# Erstellen der Subplots
fig = make_subplots(rows=2, cols=1)

# Hinzufügen der Line Plots zu den Subplots
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=df_1.E, mode='lines'), row=1, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=rolling_mean_E, mode='lines'), row=1, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=df_1.SV, mode='lines'), row=2, col=1)
fig.add_trace(go.Scatter(x=df_1["Datum (MEZ)"], y=rolling_mean_sv, mode='lines'), row=2, col=1)



# Anpassung der Layout-Eigenschaften
fig.update_layout(height=800,  title_text="Visualisierung der Daten")

fig.update_traces(
    name="E",
    row=1, col=1,
)
fig.update_traces(
    name="SV",
    row=2, col=1,
)

# Anzeigen der Subplots
fig.show()

In [42]:
# Plotly-Figur erstellen
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_1['Datum (MEZ)'], y=df_1['SE'], name='Werte von E'))
fig.add_trace(go.Scatter(x=df_1['Datum (MEZ)'], y=rolling_mean_se, name='Gleitender Durchschnitt'))

# Layout anpassen
fig.update_layout(
    title='Menge an verbauchtem Strom aus der Photovoltaic anlage über die Zeit',
    xaxis_title='Zeitschritt',
    yaxis_title='Wert von E',
    hovermode='x'
)

# Plot anzeigen
fig.show()

## Aufgabe 3

In [46]:
# wie viel kWH für eigen verbauch aus PV
np.array(se_values).sum()

424897.3996

In [55]:
# wie viel kWH für eigen verbauch aus batterie ()*0.9 ?
(np.array(bm_values)*0.9).sum()

26330.489082

In [51]:
#Gesamtkosten (E)
(np.array(E_values)*0.22).sum()

130367.10889796002

In [52]:
#ersparnis durch pv (SE)
(np.array(se_values)*0.22).sum()

93477.427912

In [53]:
#ersparnis durch batterie (BM)
(np.array(bm_values)*0.22*0.9).sum()

5792.70759804

## ✏ Aufgabe 2: Variabler Strompreis (10+5 Punkte)
Sie haben nun eine realistische Baseline, gegen die Sie alle weiteren Optionen vergleichen können. Als nächstes möchten Sie das Potential des dynamischen Strompreistarifes berechnen. Sie haben sich dafür bereits die relevanten historischen Strompreisdaten besorgt (Spalte `Preis [EUR/kWh]`). Der Tarif wirkt zunächst nur in eine Richtung, d.h. der Einkaufspreis ist variabel, aber die Einspeisevergütung liegt nach wie vor bei konstant 4 ct/kWh. Es kann sich durchaus lohnen, Energie aus dem Netz zu beziehen und in die Batterie einzuspeichern, wenn der Strompreis gerade niedrig ist. 

Insgesamt ergibt sich folgendes Bild:

<div>
<img src="Aufgabe2.png" width="750"/>
</div>

Erweitern Sie nun ihr Modell aus Aufgabe 1 und entwickeln Sie ein lineares Programm (mathematische Formulierung, Formulierung als Python Code und Lösung mit Gurobi) für das optimale Ein- und Ausspeichern von Strom in den Batteriespeicher bei variablem Strompreis beim Stromkauf. Berechnen Sie dieselben Kenngrößen wie in Aufgabe 1 und vergleichen Sie die Lösungen. Heben Sie exemplarisch 2-3 typische Situationen (einige Stunden oder Tage) hervor, bei denen sich die Lösungen sichtbar unterscheiden.

In [ ]:
# TO DO

## ✏ Aufgabe 3: Dimensionierung der Batterie (10+5 Punkte)
Simulieren Sie das Einsparpotential für unterschiedliche Größen von Batteriespeichern. Variieren Sie dafür die Batteriegröße in 100 kWh-Schritten zwischen 0 und 1000 kWh und berechnen Sie für jede Größe das Einsparpotential (für jede Batteriegröße ist ein LP zu lösen).

In [ ]:
# TO DO

## ✏ Aufgabe 4: Einspeisung ins Netz (10+5 Punkte)
Sie haben nun ein gutes Verständnis des Einsparpotentials ihrer aktuellen Anlage gewonnen sowie der Potentiale, die sich durch unterschiedliche Batteriespeicher realisieren lassen könnten. Bisher gehen Ihre Modelle von einer konstanten Einspeisevergütung aus. Untersuchen Sie nun auch noch das Potential, das sich bietet, wenn Sie zusätzlich als *Stromlieferant* am Strommarkt teilnehmen:

<div>
<img src="Aufgabe4.png" width="750"/>
</div>

Wir nehmen an, dass dies unter folgenden Bedingungen möglich ist:
- Pro Zeiteinheit müssen Sie entscheiden, ob Sie Strom zum pauschalen Preis einspeisen möchten oder zum variablen Preis.
- Die Einspeisung kann aus der PV-Anlage und/oder der Batterie erfolgen.
- Falls Sie während einer Zeiteinheit zum variablen Preis ins Netz einspeisen möchten, so ist dies nur möglich, wenn Sie mindestens 100 kWh einspeisen (kombiniert aus PV-Anlage und Batterie).
- Falls Sie zum variablen Preis ins Netz einspeisen möchten, so ist dies zum Marktpreis abzüglich 5 ct/kWh möglich.

Erweitern Sie nun ihr Modell aus Aufgabe 2 und entwickeln Sie ein lineares Programm für das optimale Ein- und Ausspeichern von Strom in den Batteriespeicher bei variablem Strompreis beim Stromkauf und -verkauf (mathematische Formulierung, Formulierung als Python Code und Lösung mit Gurobi). Berechnen Sie dieselben Kenngrößen wie in Aufgabe 2 und vergleichen Sie die Lösungen. Heben Sie exemplarisch 2-3 typische Situationen (einige Stunden oder Tage) hervor, bei denen sich die Lösungen sichtbar unterscheiden.

In [ ]:
# TO DO

## ✏ Aufgabe 5: Validierung (10+5 Punkte)
Bei all Ihren Betrachtungen haben Sie bisher einen Aspekt außer Acht gelassen: Die Berechnungen wurden *a posteriori* durchgeführt, d.h. sie wurden im Nachhinein auf bekannten Daten angestellt. In der Realität weiß man aber zum Zeitpunkt der Entscheidung (ein-/ausspeichern) noch nicht, wie sich der Strompreis, der Verbrauch und die produzierte Strommenge zukünftig entwickeln werden. Das so berechnete Einsparpotential ist deshalb wahrscheinlich ein wenig zu optimistisch.

In der Datei `energy_2020_scenarios.pkl` finden Sie 100 verschiedene Szenarien, wie der Strompreis tatsächlich sein könnte. Evaluieren Sie anhand der verschiedenen Szenarien, wie hoch die Stromkosten mit dem optimalen Ein- und Ausspeichern wie in den Aufgaben 1, 2 und 4 berechnet tatsächlich sein könnten:
- Berechnen Sie für jedes Szenario und für jedes der drei Modelle die Stromkosten.
- Visualisieren Sie die Ergebnisse der Simulation in einem geeigneten (vergleichenden) statistischen Plot.

Was müssten Sie zusätzlich beachten, wenn Sie eine derartige Simulation für verschiedene Szenarien des Strombedarfs und der Stromerzeugung machen würden?

In [ ]:
# TO DO